## Using Tutorial from 

https://towardsdatascience.com/how-to-generate-music-using-a-lstm-neural-network-in-keras-68786834d4c5

In [1]:
from music21 import converter, instrument, note, chord, stream
import glob
import numpy as np
from keras.models import Sequential
from keras.layers import Dense, LSTM, Dropout
from keras.callbacks import EarlyStopping, ModelCheckpoint
import tensorflow as tf
from tqdm import tqdm
np.random.seed(100)
tf.set_random_seed(100)

Using TensorFlow backend.


In [2]:
notes = []
for file in glob.glob('./midi/*'):
    music = converter.parse(file)
    parts = instrument.partitionByInstrument(music)
    if parts:
        notes_to_parse = parts.parts[0].recurse()
    else:
        notes_to_parse = music.flat.notes
    for element in notes_to_parse:
        if isinstance(element, note.Note):
            notes.append(str(element.pitch))
        elif isinstance(element, chord.Chord):
            notes.append('.'.join(str(n) for n in element.normalOrder))
    print(file,' Complete')

./midi\appass_1.mid  Complete
./midi\appass_2.mid  Complete
./midi\appass_3.mid  Complete
./midi\bach_846.mid  Complete
./midi\bach_847.mid  Complete
./midi\bach_850.mid  Complete
./midi\beethoven_hammerklavier_1.mid  Complete
./midi\beethoven_hammerklavier_2.mid  Complete
./midi\beethoven_hammerklavier_3.mid  Complete
./midi\beethoven_hammerklavier_4.mid  Complete
./midi\beethoven_les_adieux_1.mid  Complete
./midi\beethoven_les_adieux_2.mid  Complete
./midi\beethoven_les_adieux_3.mid  Complete
./midi\beethoven_opus10_1.mid  Complete
./midi\beethoven_opus10_2.mid  Complete
./midi\beethoven_opus10_3.mid  Complete
./midi\beethoven_opus22_1.mid  Complete
./midi\beethoven_opus22_2.mid  Complete
./midi\beethoven_opus22_3.mid  Complete
./midi\beethoven_opus22_4.mid  Complete
./midi\beethoven_opus90_1.mid  Complete
./midi\beethoven_opus90_2.mid  Complete
./midi\elise.mid  Complete
./midi\grieg_album.mid  Complete
./midi\grieg_berceuse.mid  Complete
./midi\grieg_brooklet.mid  Complete
./midi\g

In [3]:
len(notes)

192768

In [4]:
seq_n = 10
pitchnames = sorted(set(item for item in notes))
note_to_int = dict((note, number) for number, note in enumerate(pitchnames))
print(note_to_int)

{'7.8.10.1.3': 197, '7.9.0.3': 200, 'C#5': 260, 'B4': 254, '10.1.4.6': 55, '4.6.9.0': 135, '5.6': 148, '5.9': 160, '3.6': 116, 'C#6': 261, '8.1': 207, '8.11.2': 215, 'E-2': 277, '0.3.7': 15, '1.2.5': 25, '7.10': 185, 'G6': 315, 'D6': 274, '3.7.8': 124, '7.11.1': 193, '2.6.7': 101, '9.0.2.5': 222, '2.3.5.8.10': 85, '6.7.10': 170, '4.5.7.10.0': 130, 'F#7': 296, '5.8.11.1': 159, '0.3.6.9': 14, '4.8': 141, 'B-4': 248, '1.4.6': 35, 'F4': 300, '11.2': 73, '6.11': 167, 'F6': 302, 'C3': 265, 'A0': 238, 'F7': 303, '9': 219, '0.4.7': 19, '2.4.9': 91, '3.5.8.11': 114, '1.2': 24, '10.1.4': 54, '8.10': 208, '11.1.2': 70, '1.5.9': 43, 'D4': 272, '5.11': 147, '4.6.9': 134, '2.5.8': 95, '8.0.2': 205, 'C#2': 257, 'F#4': 293, '1.4.7.9': 38, '11.2.6': 79, 'G#2': 305, '1.3.7': 31, 'F#6': 295, '4.7.10.0': 138, 'C6': 268, '2.8': 106, '10.1.3': 52, '0.2.7': 8, '6.9.0.1': 178, '1': 23, '2.4.7': 88, '10.2.5': 63, '7.9.0': 199, 'G3': 312, '6.10': 164, '4.6': 132, '0.6': 22, '10.1': 51, 'B-2': 246, '1.4.8': 39, 

In [5]:
network_inp = []
network_out = []

for i in range(len(notes) - seq_n):
    seq_in = notes[i:i + seq_n]
    seq_out = notes[i + seq_n]
    network_inp.append([note_to_int[char] for char in seq_in])
    network_out.append(note_to_int[seq_out])

In [6]:
n_patterns = len(network_inp)
n_vocab = len(note_to_int)

In [7]:
print(n_patterns)
print(n_vocab)

192758
316


In [8]:
network_inp = np.reshape(network_inp, (n_patterns, seq_n, 1))
network_inp = network_inp / float(n_vocab)
print(network_inp.shape)
network_out = np.eye(n_vocab)[network_out]
print(network_out.shape)

(192758, 10, 1)
(192758, 316)


In [9]:
filepath = './weights_best.hdf5'

In [10]:
model = Sequential()
model.add(LSTM(256, input_shape = (network_inp.shape[1], network_inp.shape[2]), 
               return_sequences = True))
model.add(Dropout(0.3))
model.add(LSTM(256))
model.add(Dense(256))
model.add(Dropout(0.3))
model.add(Dense(n_vocab, activation='softmax'))
callbacks = [EarlyStopping(monitor='loss', patience=10, verbose=0, mode='auto'), 
             ModelCheckpoint(filepath=filepath, monitor='loss', verbose=0, mode='max')]
model.compile(loss = 'categorical_crossentropy', optimizer='rmsprop')
model.load_weights('weights_best.hdf5')

In [26]:
model.fit(network_inp, network_out, epochs=250, batch_size=32, verbose=1, callbacks=callbacks)

Epoch 1/250
14503/14503 [==============================] - ETA: 745s - loss: 5.4337 - ETA: 383s - loss: 5.4247 - ETA: 200s - loss: 5.3138 - ETA: 164s - loss: 5.3958 - ETA: 123s - loss: 5.3717 - ETA: 99s - loss: 5.2997  - ETA: 92s - loss: 5.2569 - ETA: 79s - loss: 5.2142 - ETA: 71s - loss: 5.1725 - ETA: 64s - loss: 5.1417

In [12]:
start = np.random.randint(0, len(network_inp) - 1)
int_to_note = dict((number, note) for number, note in enumerate(pitchnames))

pattern = network_inp[start].reshape((seq_n))
pattern = pattern.tolist()
prediction_output = []

for note_index in tqdm(range(14386)):
    if note_index%500==0:
        start = np.random.randint(0, len(network_inp) - 1)
        pattern = network_inp[start].reshape((seq_n))
        pattern = pattern.tolist()
    prediction_input = np.reshape(pattern, (1, len(pattern), 1))
    prediction = model.predict(prediction_input, verbose=1)

    index = np.argmax(prediction)
    result = int_to_note[index]
    prediction_output.append(result)

    pattern.append(index / n_vocab)
    pattern = [x for x in pattern]
    pattern = pattern[1:len(pattern)+1]

  0%|                                                                                        | 0/14386 [00:00<?, ?it/s]

1/1 [==============================] - 0s


  0%|                                                                              | 1/14386 [00:00<1:16:28,  3.13it/s]

1/1 [==============================] - 0s


  0%|                                                                               | 10/14386 [00:00<54:22,  4.41it/s]

...

100%|███████████████████████████████████████████████████████████████████████████▉| 14376/14386 [03:01<00:00, 80.51it/s]

1/1 [==============================] - 0s


100%|███████████████████████████████████████████████████████████████████████████▉| 14385/14386 [03:01<00:00, 80.90it/s]

1/1 [==============================] - 0s


100%|████████████████████████████████████████████████████████████████████████████| 14386/14386 [03:01<00:00, 79.22it/s]


In [13]:
prediction_output[14000:14100]

['F5',
 'E4',
 'B3',
 'F5',
 'B3',
 'G5',
 'F4',
 'G#3',
 'G4',
 'F4',
 'C5',
 'B-4',
 'G#5',
 'E-5',
 'B-5',
 'B-5',
 'G5',
 'C5',
 'B-2',
 'D3',
 'G3',
 'E-4',
 'F5',
 'B4',
 'E5',
 'F5',
 'C#4',
 'E4',
 'E-5',
 'F5',
 'B-4',
 'E-5',
 'F#4',
 'E-3',
 'D4',
 'B4',
 'F5',
 'F#4',
 'E3',
 'D4',
 'C5',
 'G#4',
 'F4',
 'C4',
 'B4',
 'G#4',
 'F4',
 'C6',
 'G#5',
 'G#4',
 'F4',
 'D4',
 'G#2',
 'G#3',
 'E-3',
 'E-3',
 'G#5',
 'E3',
 'F3',
 'F4',
 'F5',
 'F4',
 'G#3',
 'G#4',
 'B4',
 'D5',
 'D5',
 'F3',
 'C3',
 'C#4',
 'G#4',
 'B-4',
 'G#3',
 'F5',
 'G#5',
 'F4',
 'C4',
 'D5',
 'G#4',
 'E-4',
 'G#3',
 'E-4',
 'C5',
 'D4',
 'C5',
 'G#5',
 'C3',
 'G#4',
 'E-5',
 'C#4',
 'F4',
 'E-4',
 'G#5',
 'G#3',
 'C4',
 'E-4',
 'G#4',
 'C5',
 'E-3',
 'C5']

In [14]:
offset = 0
output_notes = []

# create note and chord objects based on the values generated by the model

for pattern in prediction_output:
    # pattern is a chord
    if ('.' in pattern) or pattern.isdigit():
        notes_in_chord = pattern.split('.')
        notes = []
        for current_note in notes_in_chord:
            new_note = note.Note(int(current_note))
            new_note.storedInstrument = instrument.Piano()
            notes.append(new_note)
        new_chord = chord.Chord(notes)
        new_chord.offset = offset
        output_notes.append(new_chord)
    # pattern is a note
    else:
        new_note = note.Note(pattern)
        new_note.offset = offset
        new_note.storedInstrument = instrument.Piano()
        output_notes.append(new_note)

    # increase offset each iteration so that notes do not stack
    offset += 0.5

In [15]:
midi_stream = stream.Stream(output_notes)

midi_stream.write('midi', fp='test_output.mid')

'test_output.mid'